In [ ]:

#### READ ME ###

################ When load this in Paraview !!!!!!!!!!!! => Work the first time then bug !!!!!!!!!!!

from __future__ import print_function
from fenics import *
from mshr import *
from dolfin import *
import matplotlib.pyplot as plt
import time
from math import *

set_log_level(40)


dt = 0.01
Radius_Droplet = 5


mesh = generate_mesh(Circle(Point(0,0),20.0),100)

V = FunctionSpace(mesh, 'CG', 1)
Phi_u = Function(V)
v = TestFunction(V)


Phi_u0 = Function(V)
Phi_tot = Function(V)

tol = 1E-14


Phi_u0_int = 0.01
Phi_u0_ext = 0.05
Phi_u0_notbleach = 0.35

Phi_u0 = interpolate(Expression('sqrt(x[1]*x[1]+x[0]*x[0]) <= Radius_Droplet && atan2(x[1],x[0]) < 0  ? Phi_u0_int : sqrt(x[1]*x[1]+x[0]*x[0]) <= Radius_Droplet && atan2(x[1],x[0]) >= 0 ?  Phi_u0_notbleach : Phi_u0_ext' , degree=2,tol=tol,Phi_u0_int = Phi_u0_int,Phi_u0_ext=Phi_u0_ext, Phi_u0_notbleach = Phi_u0_notbleach, Radius_Droplet=Radius_Droplet),V)







Phi_tot_int = 0.35
Phi_tot_ext = 0.05

Phi_tot = interpolate(Expression('sqrt(x[1]*x[1]+x[0]*x[0]) <= Radius_Droplet ? Phi_tot_int : Phi_tot_ext', degree=2,tol=tol,Phi_tot_int=Phi_tot_int,Phi_tot_ext=Phi_tot_ext,Radius_Droplet=Radius_Droplet),V)


u_D = Constant(0.05)

def boundary(x, on_boundary):
    tol = 1E-14
    return on_boundary

bc = DirichletBC(V, u_D, boundary)

Form = (inner((Phi_u-Phi_u0)/dt, v) - inner(((1-Phi_tot)/Phi_tot)*Phi_u*grad(Phi_tot) - (1-Phi_tot)*grad(Phi_u), grad(v))) *dx



vtkfile = File('Disk/Phi0.pvd')
vtkfile << Phi_u0



t = 0
cFile = XDMFFile('test.xmdf')
cFile.write(Phi_u0, t)

ti = time.time()
for i in range(200):
    solve(Form == 0, Phi_u, bc)
    assign(Phi_u0, Phi_u)
    t += dt
    cFile.write(Phi_u0, t)
    print(time.time() - ti)

cFile.close()

    
